In [15]:
import pandas as pd
import numpy as np
import glob
import os
import plotly.express as px
from shapely.geometry.polygon import Polygon
import geopandas as gpd
from plotly.offline import plot
import plotly.graph_objects as go
import shapely
from shapely import wkt
import pandas as pd
import json
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import nbformat

filepath = '/Users/kmak/Desktop/EC.719/Building Energy Visualization/net-zero-dlab/Data files'


	
init_notebook_mode(connected=True)

In [16]:
electricity = pd.read_csv(filepath + '/Electricity.csv') # read csv file
electricity['geometry'] = gpd.GeoSeries.from_wkt(electricity['geometry']) # convert type of geometry column

steam = pd.read_csv(filepath + '/Steam.csv')
steam['geometry'] = gpd.GeoSeries.from_wkt(steam['geometry'])

chilledWater = pd.read_csv(filepath + '/Chilled Water.csv')
chilledWater['geometry'] = gpd.GeoSeries.from_wkt(chilledWater['geometry'])

        
electricity

BUILDING_NUMBER   2010-02-01   2010-03-01   2010-04-01   2010-05-01  \
0                 1   523.113923  1083.740129   188.827638  1269.482415   
1                10   659.442795  1366.179531   238.039685  1600.324983   
2                11   121.939664   252.626847    44.017461   295.927578   
3                12   259.695170   232.070348   263.398275   242.654061   
4                13  1739.363777  1819.541973  2089.465904  1782.449489   
..              ...          ...          ...          ...          ...   
132             W91  1275.328884  1280.462036  1415.036626  1340.892614   
133             W92   941.657408   847.540800   789.291136   849.724480   
134             W97          NaN          NaN          NaN          NaN   
135             W98   436.097990   424.224196   392.574487   402.390811   
136            WW15    62.780800    63.599680    51.316480    46.676160   

      2010-06-01   2010-07-01   2010-08-01   2010-09-01   2010-10-01  ...  \
0     553.069824   498.110285   743.412834   263.254929   414.327961  ...   
1     697.204227   627.927153   937.155192   331.863055   522.305042  ...   
2     128.922662   116.113673   173.295075    61.365740    96.584487  ...   
3     258.282188   246.998810   286.552067          NaN    47.857086  ...   
4    1990.748292  1698.387299  1694.138114  1720.793644  1632.106839  ...   
..           ...          ...          ...          ...          ...  ...   
132  1415.435947  1229.331883  1440.142654  1593.894891  1287.503055  ...   
133   782.248768   834.984640   947.990080   838.642304   850.870912  ...   
134          NaN          NaN          NaN          NaN          NaN  ...   
135   387.156262   442.713824   528.542718   479.908039   463.847786  ...   
136    44.765440    79.158400   116.417440   115.189120    83.252800  ...   

      2019-06-01   2019-07-01   2019-08-01   2019-09-01   2019-10-01  \
0     655.012721   215.377365   574.732135    23.809088  1145.150238   
1     812.973187   267.319812   713.337478    29.549754  1421.313133   
2     150.335824    49.433892   131.912450     5.464213   262.831717   
3    1332.162160  1349.786892  1454.794663  1458.944871  1404.132091   
4    1934.792157  1971.877815  2015.093221  2032.574607  1997.130602   
..           ...          ...          ...          ...          ...   
132  1139.535853  1104.163521  1206.734410  1153.266352  1040.620287   
133   841.644864   897.820032   877.020480   833.183104   847.158656   
134    69.277248    93.352320    94.007424    85.163520    85.409184   
135   420.198039   451.097111   424.824711   388.759871   414.131503   
136    51.998880    58.413440    72.743840    74.245120    62.780800   

      2019-11-01   2019-12-01   2020-01-01  \
0     625.671160   822.488631   491.611933   
1     776.556477  1023.958021   612.032812   
2     143.601975   189.793517   113.444707   
3    1461.282776  1397.056942  1381.196731   
4    2050.888765  1905.621246  2052.250552   
..           ...          ...          ...   
132  1058.859359   977.080466   994.445810   
133   763.305344   843.446400   734.972096   
134    66.411168    68.540256    61.334112   
135   372.563107   381.372891   352.609731   
136    55.001440    58.413440    59.368800   

                                              geometry         area  
0    POLYGON ((-71.09220 42.35837, -71.09251 42.358...  30287.72068  
1    POLYGON ((-71.09170 42.35970, -71.09163 42.359...  24380.33563  
2    POLYGON ((-71.09260 42.35946, -71.09282 42.359...   5048.14134  
3    POLYGON ((-71.09198 42.36024, -71.09181 42.360...  37027.92652  
4    POLYGON ((-71.09197 42.35997, -71.09235 42.359...  36498.76204  
..                                                 ...          ...  
132  POLYGON ((-71.10444 42.35468, -71.10423 42.354...  20177.79011  
133  POLYGON ((-71.10442 42.35509, -71.10439 42.355...  28674.24162  
134  POLYGON ((-71.10651 42.35453, -71.10679 42.354...  18023.71972  
135  POLYGON ((-71.10627 42.35393, -71.10627 42.353...  1272

In [17]:
electricity = electricity.dropna(subset=['geometry'], axis=0, inplace=False)
steam = steam.dropna(subset=['geometry'], axis=0, inplace=False)
chilledWater = chilledWater.dropna(subset=['geometry'], axis=0, inplace=False)

In [18]:
def df_to_geojson(df, properties, geometry='geometry'):
    # create a new python dict to contain our geojson data, using geojson format
    geojson = {'type':'FeatureCollection', 'features':[]}

    # loop through each row in the dataframe and convert each row to geojson format
    for _, row in df.iterrows():
        # create a feature template to fill in
        feature = {'type':'Feature',
                   'properties':{},
                   'geometry':{'type':'Polygon',
                               'coordinates':[]}}

        polygon = row['geometry']
        feature['geometry']['coordinates'] = [np.asarray(polygon.exterior.coords).tolist()]

        # for each column, get the value and add it as a new feature property
        for prop in properties:
            feature['properties'][prop] = row[prop]
        
        # add this feature (aka, converted dataframe row) to the list of features inside our dict
        geojson['features'].append(feature)
    
    return geojson

In [19]:
properties=['BUILDING_NUMBER']
ejson = df_to_geojson(electricity, properties)
sjson = df_to_geojson(steam, properties)
cjson = df_to_geojson(chilledWater, properties)

print(json.dumps(ejson['features'][0], indent=4))

{
    "type": "Feature",
    "properties": {
        "BUILDING_NUMBER": "1"
    },
    "geometry": {
        "type": "Polygon",
        "coordinates": [
            [
                [
                    -71.09220231,
                    42.3583671
                ],
                [
                    -71.09251327,
                    42.35826301
                ],
                [
                    -71.09228599,
                    42.35788799
                ],
                [
                    -71.09192792,
                    42.35800848
                ],
                [
                    -71.09193236,
                    42.35801969
                ],
                [
                    -71.09175402,
                    42.35807864
                ],
                [
                    -71.0917308,
                    42.358042
                ],
                [
                    -71.09171812,
                    42.35804621
                ],
             

In [20]:
fig = go.Figure()

efig = go.Choroplethmapbox(
    geojson=ejson,
    featureidkey = 'properties.BUILDING_NUMBER',
    locations = electricity.BUILDING_NUMBER,
    z = electricity['2010-02-01'],
    colorscale='Reds',
    zmin = 0,
    zmax = 6000,
    showscale=True,
    colorbar={"title": 'MMBTU'},
    visible=True
 )

layout = go.Layout(
      title='Electricity Usage',
      mapbox_style='carto-positron',
      autosize=True,
      mapbox_center={'lat':42.359, 'lon':-71.095},
      mapbox_zoom=14,
)

fig.update_layout(layout)

fig.add_trace(efig)
iplot(fig)

In [21]:
months = electricity.columns[1:-2]

sliders_dict = [dict(active=months[0],
                    visible = True,
                    yanchor='top',
                    xanchor='left',
                    currentvalue=dict(font=dict(size=20),
                     prefix='Date:',
                     visible=True,
                     xanchor='right'),
                     steps=[]
                   )]

eframes = []

for month in months:
    frame = go.Frame(
        data = [
            go.Choroplethmapbox(
                featureidkey = 'properties.BUILDING_NUMBER',
                locations = electricity.BUILDING_NUMBER,
                z = electricity[month],
                colorscale='Reds',
                zmin = 0,
                zmax = 6000,
                showscale=True,
                colorbar={"title": 'MMBTU'},
                
            )
        ],
        layout=go.Layout(
            annotations = [dict(
                xref="x domain",
                yref="y domain",
                x=0.5,
                y=-0.1,
                text=month,
                showarrow = False,
                font=dict(size=16)
            )]
        )
    )
    eframes.append(frame)
    
    slider_step = dict(
        args=[[month],
             dict(mode='immediate',
                 frame = dict(duration=300, redraw=True))],
        method='animate',
        label=month
    )
    
    sliders_dict[0]["steps"].append(slider_step)
    
layout["updatemenus"] = [
    dict(type="buttons",
          buttons=[dict(label="Play",
                        method="animate",
                        args=[None,
                              dict(frame=dict(duration=1000,
                                              redraw=True),
                                   fromcurrent=True)]),
                   dict(label="Pause",
                        method="animate",
                        args=[[None],
                              dict(frame=dict(duration=0,
                                              redraw=True),
                                   mode="immediate")])],
          direction="left",
          pad={"r": 10, "t": 35},
          showactive=False,
          x=0.1,
          xanchor="right",
          y=0,
          yanchor="top")]

fig=go.Figure(data=efig, layout=layout,frames=eframes)

fig.show()

In [22]:
sfig = go.Choroplethmapbox(
    geojson=sjson,
    featureidkey = 'properties.BUILDING_NUMBER',
    locations = steam.BUILDING_NUMBER,
    z = steam['2010-02-01'],
    colorscale='Reds',
    zmin = 0,
    zmax = 12000,
    showscale=True,
    colorbar={"title": 'MMBTU'},
    visible=False
 )

cfig = go.Choroplethmapbox(
    geojson=cjson,
    featureidkey = 'properties.BUILDING_NUMBER',
    locations = chilledWater.BUILDING_NUMBER,
    z = chilledWater['2010-02-01'],
    colorscale='Reds',
    zmin = 0,
    zmax = 6000,
    showscale=True,
    colorbar={"title": 'MMBTU'},
    visible=False
 )

In [24]:
fig = go.Figure()

fig.update_layout(
      title='Electricity Usage',
      mapbox_style='carto-positron',
      autosize=True,
      mapbox_center={'lat':42.359, 'lon':-71.095},
      mapbox_zoom=14,
)

fig.update_layout(
    updatemenus=[
        dict(
            type="buttons",
            direction="right",
            active=0,
            x=0.57,
            y=1.2,
            buttons=list([
                dict(label="Electricity",
                     method="update",
                     args=[{"visible": [True, False, False]},
                           {"title": "Electricity Usage",
                            "annotations": []}]),
                dict(label="Steam",
                     method="update",
                     args=[{"visible": [False, True, False]},
                           {"title": "Steam Usage",
                            "annotations": []}]),
                dict(label="Chilled Water",
                     method="update",
                     args=[{"visible": [False, False, True]},
                           {"title": "Chilled Water Usage",
                            "annotations": []}])
            ]),
        )
    ])

fig.add_trace(efig)
fig.add_trace(sfig)
fig.add_trace(cfig)

iplot(fig)

In [10]:
months = electricity.columns[1:-2]
electricityNorm = electricity
steamNorm = steam
chilledWaterNorm = chilledWater

for m in months:
    electricityNorm[m] = electricityNorm[m]/electricityNorm['area']
    steamNorm[m] = steamNorm[m]/steamNorm['area']
    chilledWaterNorm[m] = chilledWaterNorm[m]/chilledWaterNorm['area']


/var/folders/09/m5s9tp9d3jv_16bdmpjm79rw0000gn/T/ipykernel_47305/3857758549.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [11]:
electricityNorm.fillna(-1)

BUILDING_NUMBER  2010-02-01  2010-03-01  2010-04-01  2010-05-01  \
0                 1    0.017271    0.035782    0.006234    0.041914   
1                10    0.027048    0.056036    0.009764    0.065640   
2                11    0.024155    0.050044    0.008720    0.058621   
3                12    0.007013    0.006267    0.007114    0.006553   
4                13    0.047655    0.049852    0.057248    0.048836   
..              ...         ...         ...         ...         ...   
132             W91    0.063205    0.063459    0.070128    0.066454   
133             W92    0.032840    0.029558    0.027526    0.029634   
134             W97   -1.000000   -1.000000   -1.000000   -1.000000   
135             W98    0.034277    0.033343    0.030856    0.031627   
136            WW15    0.001533    0.001553    0.001253    0.001139   

     2010-06-01  2010-07-01  2010-08-01  2010-09-01  2010-10-01  ...  \
0      0.018261    0.016446    0.024545    0.008692    0.013680  ...   
1      0.028597    0.025755    0.038439    0.013612    0.021423  ...   
2      0.025539    0.023001    0.034328    0.012156    0.019133  ...   
3      0.006975    0.006671    0.007739   -1.000000    0.001292  ...   
4      0.054543    0.046533    0.046416    0.047147    0.044717  ...   
..          ...         ...         ...         ...         ...  ...   
132    0.070148    0.060925    0.071373    0.078993    0.063808  ...   
133    0.027281    0.029120    0.033061    0.029247    0.029674  ...   
134   -1.000000   -1.000000   -1.000000   -1.000000   -1.000000  ...   
135    0.030430    0.034797    0.041543    0.037720    0.036458  ...   
136    0.001093    0.001932    0.002842    0.002812    0.002032  ...   

     2019-06-01  2019-07-01  2019-08-01  2019-09-01  2019-10-01  2019-11-01  \
0      0.021626    0.007111    0.018976    0.000786    0.037809    0.020658   
1      0.033345    0.010965    0.029259    0.001212    0.058298    0.031852   
2      0.029780    0.009792    0.026131    0.001082    0.052065    0.028447   
3      0.035977    0.036453    0.039289    0.039401    0.037921    0.039464   
4      0.053010    0.054026    0.055210    0.055689    0.054718    0.056191   
..          ...         ...         ...         ...         ...         ...   
132    0.056475    0.054722    0.059805    0.057155    0.051573    0.052476   
133    0.029352    0.031311    0.030586    0.029057    0.029544    0.026620   
134    0.003844    0.005179    0.005216    0.004725    0.004739    0.003685   
135    0.033027    0.035456    0.033391    0.030556    0.032550    0.029283   
136    0.001269    0.001426    0.001776    0.001813    0.001533    0.001343   

     2019-12-01  2020-01-01  \
0      0.027156    0.016231   
1      0.041999    0.025104   
2      0.037597    0.022473   
3      0.037730    0.037301   
4      0.052211    0.056228   
..          ...         ...   
132    0.048424    0.049284   
133    0.029415    0.025632   
134    0.003803    0.003403   
135    0.029975    0.027715   
136    0.001426    0.001449   

                                              geometry         area  
0    POLYGON ((-71.09220 42.35837, -71.09251 42.358...  30287.72068  
1    POLYGON ((-71.09170 42.35970, -71.09163 42.359...  24380.33563  
2    POLYGON ((-71.09260 42.35946, -71.09282 42.359...   5048.14134  
3    POLYGON ((-71.09198 42.36024, -71.09181 42.360...  37027.92652  
4    POLYGON ((-71.09197 42.35997, -71.09235 42.359...  36498.76204  
..                                                 ...          ...  
132  POLYGON ((-71.10444 42.35468, -71.10423 42.354...  20177.79011  
133  POLYGON ((-71.10442 42.35509, -71.10439 42.355...  28674.24162  
134  POLYGON ((-71.10651 42.35453, -71.10679 42.354...  18023.71972  
135  POLYGON ((-71.10627 42.35393, -71.10627 42.353...  12722.90481  
136  POLYGON ((-71.10944 42.35574, -71.10892 42.355...  40962.80174  

[112 rows x 123 columns]

In [12]:
fig = go.Figure()

efig = go.Choroplethmapbox(
    geojson=ejson,
    featureidkey = 'properties.BUILDING_NUMBER',
    locations = electricityNorm.BUILDING_NUMBER,
    z = electricityNorm['2010-02-01'],
    colorscale='Reds',
    zmin = 0,
    zmax = 0.3,
    showscale=True,
    visible=True
 )

eframes = []

for month in months:
    frame = go.Frame(
        data = [
            go.Choroplethmapbox(
                featureidkey = 'properties.BUILDING_NUMBER',
                locations = electricityNorm.BUILDING_NUMBER,
                z = electricityNorm[month],
                colorscale='Reds',
                zmin = 0,
                zmax = 0.3,
                showscale=True
            )
        ],
        layout=go.Layout(
            annotations = [dict(
                xref="x domain",
                yref="y domain",
                x=0.5,
                y=-0.1,
                text=month,
                showarrow = False,
                font=dict(size=16)
            )]
        )
    )
    eframes.append(frame)
    
layout["updatemenus"] = [
    dict(type="buttons",
          buttons=[dict(label="Play",
                        method="animate",
                        args=[None,
                              dict(frame=dict(duration=1000,
                                              redraw=True),
                                   fromcurrent=True)]),
                   dict(label="Pause",
                        method="animate",
                        args=[[None],
                              dict(frame=dict(duration=0,
                                              redraw=True),
                                   mode="immediate")])],
          direction="left",
          pad={"r": 10, "t": 35},
          showactive=False,
          x=0.1,
          xanchor="right",
          y=0,
          yanchor="top")]

fig=go.Figure(data=efig, layout=layout,frames=eframes)

fig.update_layout(
      title='Electricity Usage Per Square Area',
      mapbox_style='carto-positron',
      autosize=True,
      mapbox_center={'lat':42.359, 'lon':-71.095},
      mapbox_zoom=14,
)

fig.show()

In [13]:
sframes = []
cframes = []

for month in months:
    sframe = go.Frame(
        data = [
            go.Choroplethmapbox(
                featureidkey = 'properties.BUILDING_NUMBER',
                locations = steam.BUILDING_NUMBER,
                z = steam[month],
                colorscale='Reds',
                zmin = 0,
                zmax = 6000,
                showscale=True,
                colorbar={"title": 'MMBTU'},
                
            )
        ],
        layout=go.Layout(
            annotations = [dict(
                xref="x domain",
                yref="y domain",
                x=0.5,
                y=-0.1,
                text=month,
                showarrow = False,
                font=dict(size=16)
            )]
        )
    )
    
    cframe = go.Frame(
        data = [
            go.Choroplethmapbox(
                featureidkey = 'properties.BUILDING_NUMBER',
                locations = chilledWater.BUILDING_NUMBER,
                z = chilledWater[month],
                colorscale='Reds',
                zmin = 0,
                zmax = 6000,
                showscale=True,
                colorbar={"title": 'MMBTU'},
                
            )
        ],
        layout=go.Layout(
            annotations = [dict(
                xref="x domain",
                yref="y domain",
                x=0.5,
                y=-0.1,
                text=month,
                showarrow = False,
                font=dict(size=16)
            )]
        )
    )
    
    sframes.append(sframe)
    cframes.append(cframe)